In [1]:
!git clone https://github.com/neonbjb/tortoise-tts.git

Cloning into 'tortoise-tts'...


In [ ]:
%cd tortoise-tts
!python setup.py install

In [1]:
# Imports used through the rest of the notebook.
import torch
import torchaudio
import torch.nn as nn
import torch.nn.functional as F

import IPython

import os
print(os.getcwd())
# from tortoise_tts.tortoise.tts import TextToSpeech
# from tortoise-tts.tortoise.tts import TextToSpeech


from tortoise.api import TextToSpeech
from tortoise.utils.audio import load_audio, load_voice, load_voices

# This will download all the models used by Tortoise from the HF hub.
# tts = TextToSpeech()
# If you want to use deepspeed the pass use_deepspeed=True nearly 2x faster than normal
tts = TextToSpeech( kv_cache=True)

g:\rp-tibedm\tortoise


c:\Users\tibed\anaconda3\envs\tortoise\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
Some weights of the model checkpoint at jbetker/wav2vec2-large-robust-ft-libritts-voxpopuli were not used when initializing Wav2Vec2ForCTC: ['wav2vec2.encoder.pos_conv_embed.conv.weight_v', 'wav2vec2.encoder.pos_conv_embed.conv.weight_g']
- This IS expected if you are initializing Wav2Vec2ForCTC from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing Wav2Vec2ForCTC from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of Wav2Vec2ForCTC were 

In [3]:
# This is the text that will be spoken.
text = "Joining two modalities results in a surprising increase in generalization! What would happen if we combined them all?"

# Here's something for the poetically inclined.. (set text=)
"""
Then took the other, as just as fair,
And having perhaps the better claim,
Because it was grassy and wanted wear;
Though as for that the passing there
Had worn them really about the same,"""

# Pick a "preset mode" to determine quality. Options: {"ultra_fast", "fast" (default), "standard", "high_quality"}. See docs in api.py
preset = "ultra_fast"

In [13]:
# Tortoise will attempt to mimic voices you provide. It comes pre-packaged
# with some voices you might recognize.

# Let's list all the voices available. These are just some random clips I've gathered
# from the internet as well as a few voices from the training dataset.
# Feel free to add your own clips to the voices/ folder.
%ls tortoise-tts\\tortoise\voices

IPython.display.Audio('tortoise-tts/tortoise/voices/tom/1.wav')

 Volume in drive G is Games
 Volume Serial Number is F002-617B

 Directory of g:\rp-tibedm\tortoise\tortoise-tts\tortoise\voices

09/01/2024  15:57    <DIR>          .
09/01/2024  15:59    <DIR>          ..
09/01/2024  15:57    <DIR>          angie
09/01/2024  15:57    <DIR>          applejack
09/01/2024  15:57    <DIR>          cond_latent_example
09/01/2024  15:57    <DIR>          daniel
09/01/2024  15:57    <DIR>          deniro
09/01/2024  15:57    <DIR>          emma
09/01/2024  15:57    <DIR>          freeman
09/01/2024  15:57    <DIR>          geralt
09/01/2024  15:57    <DIR>          halle
09/01/2024  15:57    <DIR>          jlaw
09/01/2024  15:57    <DIR>          lj
09/01/2024  15:57    <DIR>          mol
09/01/2024  15:57    <DIR>          myself
09/01/2024  15:57    <DIR>          pat
09/01/2024  15:57    <DIR>          pat2
09/01/2024  15:57    <DIR>          rainbow
09/01/2024  15:57    <DIR>          snakes
09/01/2024  15:57    <DIR>          tim_reynolds
09/01/2024  1

In [14]:
# Pick one of the voices from the output above
voice = 'tom'

# Load it and send it through Tortoise.
voice_samples, conditioning_latents = load_voice(voice)
gen = tts.tts_with_preset(text, voice_samples=voice_samples, conditioning_latents=conditioning_latents, 
                          preset=preset)
torchaudio.save('generated.wav', gen.squeeze(0).cpu(), 24000)
IPython.display.Audio('generated.wav')

Generating autoregressive samples..


100%|██████████| 2/2 [00:09<00:00,  4.93s/it]


Computing best candidates using CLVP


100%|██████████| 2/2 [00:00<00:00,  6.70it/s]


Transforming autoregressive outputs into audio..


100%|██████████| 30/30 [00:01<00:00, 18.32it/s]


In [15]:
gen = tts.tts_with_preset(text, voice_samples=None, conditioning_latents=None, preset=preset)
torchaudio.save('generated.wav', gen.squeeze(0).cpu(), 24000)
IPython.display.Audio('generated.wav')

Generating autoregressive samples..


100%|██████████| 2/2 [00:06<00:00,  3.34s/it]


Computing best candidates using CLVP


100%|██████████| 2/2 [00:00<00:00,  8.08it/s]


Transforming autoregressive outputs into audio..


100%|██████████| 30/30 [00:00<00:00, 40.63it/s]


In [16]:
# You can also combine conditioning voices. Combining voices produces a new voice
# with traits from all the parents.
#
# Lets see what it would sound like if Picard and Kirk had a kid with a penchant for philosophy:
voice_samples, conditioning_latents = load_voices(['pat', 'william'])

gen = tts.tts_with_preset("They used to say that if man was meant to fly, he’d have wings. But he did fly. He discovered he had to.", 
                          voice_samples=None, conditioning_latents=None, preset=preset)
torchaudio.save('captain_kirkard.wav', gen.squeeze(0).cpu(), 24000)
IPython.display.Audio('captain_kirkard.wav')

Generating autoregressive samples..


100%|██████████| 2/2 [00:06<00:00,  3.29s/it]


Computing best candidates using CLVP


100%|██████████| 2/2 [00:00<00:00,  7.98it/s]


Transforming autoregressive outputs into audio..


100%|██████████| 30/30 [00:00<00:00, 42.72it/s]


In [17]:
del tts  # Will break other cells, but necessary to conserve RAM if you want to run this cell.


In [ ]:

# Tortoise comes with some scripts that does a lot of the lifting for you. For example,
# read.py will read a text file for you.
!python3 tortoise/read.py --voice=train_atkins --textfile=tortoise/data/riding_hood.txt --preset=ultra_fast --output_path=.

IPython.display.Audio('train_atkins/combined.wav')
# This will take awhile.

In [1]:
import torch
import torchaudio
import torch.nn as nn
import torch.nn.functional as F

import IPython

from tortoise.api import TextToSpeech
from tortoise.utils.audio import load_audio, load_voice, load_voices

# This will download all the models used by Tortoise from the HuggingFace hub.
tts = TextToSpeech()

c:\Users\tibed\anaconda3\envs\tortoise\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
c:\Users\tibed\anaconda3\envs\tortoise\lib\site-packages\torch\nn\utils\weight_norm.py:30: UserWarning: torch.nn.utils.weight_norm is deprecated in favor of torch.nn.utils.parametrizations.weight_norm.
  warnings.warn("torch.nn.utils.weight_norm is deprecated in favor of torch.nn.utils.parametrizations.weight_norm.")


In [8]:
# This is the text that will be spoken.
text = "Joining two modalities results in a surprising increase in generalization! What would happen if we combined them all?"

# Here's something for the poetically inclined.. (set text=)
"""
Then took the other, as just as fair,
And having perhaps the better claim,
Because it was grassy and wanted wear;
Though as for that the passing there
Had worn them really about the same,"""

# Pick a "preset mode" to determine quality. Options: {"ultra_fast", "fast" (default), "standard", "high_quality"}. See docs in api.py
preset = "standard"

In [3]:
%cd tortoise-tts

g:\rp-tibedm\tortoise\tortoise-tts


In [6]:
voice_samples, conditioning_latents = load_voice('train_atkins')

gen = tts.tts_with_preset(text, voice_samples=voice_samples, conditioning_latents=conditioning_latents,
                            preset=preset)
torchaudio.save('generated.wav', gen.squeeze(0).cpu(), 24000)
IPython.display.Audio('generated.wav')

c:\Users\tibed\anaconda3\envs\tortoise\lib\site-packages\librosa-0.10.1-py3.10.egg\librosa\core\intervals.py:8: UserWarning: Module tortoise was already imported from c:\Users\tibed\anaconda3\envs\tortoise\lib\site-packages\tortoise_tts-3.0.0-py3.10.egg\tortoise\__init__.py, but g:\rp-tibedm\tortoise\tortoise-tts is being added to sys.path
  from pkg_resources import resource_filename


Generating autoregressive samples..


100%|██████████| 12/12 [03:17<00:00, 16.44s/it]


Computing best candidates using CLVP


100%|██████████| 12/12 [00:02<00:00,  5.73it/s]


Transforming autoregressive outputs into audio..


100%|██████████| 80/80 [00:05<00:00, 14.50it/s]


In [4]:
CUSTOM_VOICE_NAME ="obama"

text = "This is a test using the tortoise model to clone a voice and generate speech."
# Pick a "preset mode" to determine quality. Options: {"ultra_fast", "fast" (default), "standard", "high_quality"}. See docs in api.py
presets = ["ultra_fast", "fast", "standard", "high_quality"]
# preset = "ultra_fast"

voice_samples, conditioning_latents = load_voice(CUSTOM_VOICE_NAME)

for preset in presets:
    print(f"Generating with preset: {preset}")
    gen = tts.tts_with_preset(text, voice_samples=voice_samples, conditioning_latents=conditioning_latents, 
                            preset=preset)
    torchaudio.save(f'generated-{CUSTOM_VOICE_NAME}-tortoise-{preset}.wav', gen.squeeze(0).cpu(), 24000)
    # IPython.display.Audio(f'generated-{CUSTOM_VOICE_NAME}-tortoise-{preset}.wav')

c:\Users\tibed\anaconda3\envs\tortoise\lib\site-packages\tortoise_tts-3.0.0-py3.10.egg\tortoise\utils\audio.py:17: WavFileWarning: Chunk (non-data) not understood, skipping it.
  sampling_rate, data = read(full_path)


Generating with preset: ultra_fast
Generating autoregressive samples..


100%|██████████| 2/2 [00:05<00:00,  2.63s/it]


Computing best candidates using CLVP


100%|██████████| 2/2 [00:00<00:00,  7.36it/s]


...

100%|██████████| 32/32 [01:27<00:00,  2.72s/it]


Computing best candidates using CLVP


100%|██████████| 32/32 [00:05<00:00,  5.52it/s]


Transforming autoregressive outputs into audio..


100%|██████████| 400/400 [00:18<00:00, 21.92it/s]


In [5]:
gen

tensor([[[-5.6807e-04, -6.3555e-04, -5.2456e-04,  ..., -6.8772e-05,
          -7.2712e-05, -7.5294e-05]]])